In [16]:
from transformers import PegasusTokenizer, PegasusForConditionalGeneration, TFPegasusForConditionalGeneration
from rouge import Rouge

# Let's load the model and the tokenizer 
model_name = "human-centered-summarization/financial-summarization-pegasus"
tokenizer = PegasusTokenizer.from_pretrained(model_name, local_files_only=True)
model = PegasusForConditionalGeneration.from_pretrained(model_name, local_files_only=True)

Some weights of PegasusForConditionalGeneration were not initialized from the model checkpoint at human-centered-summarization/financial-summarization-pegasus and are newly initialized: ['model.decoder.embed_positions.weight', 'model.encoder.embed_positions.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [22]:
reference = "National Commercial Bank (NCB), Saudi Arabia’s largest lender by assets, agreed to buy rival Samba Financial Group for $15 billion in the biggest banking takeover this year.NCB will pay 28.45 riyals ($7.58) for each Samba share, according to a statement on Sunday, valuing it at about 55.7 billion riyals. NCB will offer 0.739 new shares for each Samba share, at the lower end of the 0.736-0.787 ratio the banks set when they signed an initial framework agreement in June.The offer is a 3.5% premium to Samba’s Oct. 8 closing price of 27.50 riyals and about 24% higher than the level the shares traded at before the talks were made public. Bloomberg News first reported the merger discussions.The new bank will have total assets of more than $220 billion, creating the Gulf region’s third-largest lender. The entity’s $46 billion market capitalization nearly matches that of Qatar National Bank QPSC, which is still the Middle East’s biggest lender with about $268 billion of assets."
for num_beams in [2, 5, 8, 12, 20]:
    for max_length in [8, 32, 64, 128, 256]:
        print(num_beams, max_length)
        input_ids = tokenizer(reference, return_tensors="pt").input_ids

        # Generate the output (Here, we use beam search but you can also use any other strategy you like)
        output = model.generate(
            input_ids, 
            max_length=max_length, 
            num_beams=5, 
            early_stopping=True
        )

        summary = tokenizer.decode(output[0], skip_special_tokens=True)
        ROUGE = Rouge()
        scores = ROUGE.get_scores(summary, reference)
        for rouge, score in scores[-1].items():
            print(score['f'])
        print('-' * 70)
    print()

2 8
0.09230769142721895
0.02312138672190853
0.09230769142721895
----------------------------------------------------------------------
2 32
0.28767123031713265
0.11578947163656512
0.2465753399061738
----------------------------------------------------------------------
2 64
0.28767123031713265
0.11578947163656512
0.2465753399061738
----------------------------------------------------------------------
2 128
0.28767123031713265
0.11578947163656512
0.2465753399061738
----------------------------------------------------------------------
2 256
0.28767123031713265
0.11578947163656512
0.2465753399061738
----------------------------------------------------------------------

5 8
0.09230769142721895
0.02312138672190853
0.09230769142721895
----------------------------------------------------------------------
5 32
0.28767123031713265
0.11578947163656512
0.2465753399061738
----------------------------------------------------------------------
5 64
0.28767123031713265
0.11578947163656512
0.24657